In [1]:
!pip install transformers

import requests

import pandas as pd

from bs4 import BeautifulSoup

from datetime import datetime

import pandas as pd

import re

from transformers import pipeline

from google.colab import drive

import pandas as pd

from pandas.io.formats.info import pprint_thing

from google.colab import drive

drive.mount('/content/drive')



Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 35.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 5.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 22.0 MB/s eta 0:00:00
Mounted at /content/drive


In [2]:

def assess_sentiment_model(text, model_name):
    sentiment_analyzer = pipeline("sentiment-analysis", model=model_name)
    result = sentiment_analyzer(text)
    sentiment = result[0]['label']
    score = result[0]['score']
    return sentiment, score


def get_bbc_content(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content, "html.parser") 
    content = soup.find("div", attrs={"class": "gel-layout__item gel-2/3@l"})
    
    if content is None:
        content = soup.find("td", attrs={"class": "storybody"})
        if content is None:
            return None

    main_body = content.find_all('p')
    text = ""
    for i in main_body:
        text += i.text
    clean_text = text.replace('\n', ' ').replace('\xa0', '')
    return clean_text

def assess_sentiment(df):
    sentiment_models = [
        ("bert-base-uncased", "sentiment_bert"),
        ("roberta-base", "sentiment_roberta"),
        ("xlnet-base-cased", "sentiment_xlnet"),
        ("distilbert-base-uncased", "sentiment_distilbert")
    ]

    for _, sentiment_column in sentiment_models:
        df[sentiment_column + "_average_score"] = None

    for index, row in df.iterrows():
        content = get_bbc_content(row["url"])

        for model_name, sentiment_column in sentiment_models:
            sentiment_scores = []

            if content is not None:
                # Truncate or split the content into smaller chunks
                max_sequence_length = 512
                if len(content) > max_sequence_length:
                    content_chunks = [content[i:i+max_sequence_length] for i in range(0, len(content), max_sequence_length)]
                else:
                    content_chunks = [content]

                # Assess sentiment for each content chunk
                for chunk in content_chunks:
                    sentiment, score = assess_sentiment_model(chunk, model_name)
                    sentiment_scores.append(score)

            # Calculate average sentiment score
            if sentiment_scores:
                average_score = sum(sentiment_scores) / len(sentiment_scores)
                df.at[index, sentiment_column + "_average_score"] = average_score

    return df


In [3]:
import requests
from bs4 import BeautifulSoup
from transformers import pipeline
import pandas as pd
from tqdm import tqdm

def assess_sentiment_model(text, model_name):
    sentiment_analyzer = pipeline("sentiment-analysis", model=model_name)
    result = sentiment_analyzer(text)
    sentiment = result[0]['label']
    score = result[0]['score']
    return sentiment, score

def get_bbc_content(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content, "html.parser") 
    content = soup.find("div", attrs={"class": "gel-layout__item gel-2/3@l"})
    
    if content is None:
        content = soup.find("td", attrs={"class": "storybody"})
        if content is None:
            return None

    main_body = content.find_all('p')
    text = ""
    for i in main_body:
        text += i.text
    clean_text = text.replace('\n', ' ').replace('\xa0', '')
    return clean_text

def process_row(row, sentiment_models):
    content = get_bbc_content(row["url"])
    for model_name, sentiment_column in sentiment_models:
        sentiment_scores = []

        if content is not None:
            # Truncate or split the content into smaller chunks
            max_sequence_length = 512
            if len(content) > max_sequence_length:
                content_chunks = [content[i:i+max_sequence_length] for i in range(0, len(content), max_sequence_length)]
            else:
                content_chunks = [content]

            # Assess sentiment for each content chunk
            for chunk in content_chunks:
                sentiment, score = assess_sentiment_model(chunk, model_name)
                sentiment_scores.append(score)

        # Calculate average sentiment score
        if sentiment_scores:
            average_score = sum(sentiment_scores) / len(sentiment_scores)
            row[sentiment_column + "_average_score"] = average_score

    return row

def assess_sentiment(df):
    sentiment_models = [
        ("bert-base-uncased", "sentiment_bert"),
        ("roberta-base", "sentiment_roberta"),
        ("xlnet-base-cased", "sentiment_xlnet"),
        ("distilbert-base-uncased", "sentiment_distilbert")
    ]

    for _, sentiment_column in sentiment_models:
        df[sentiment_column + "_average_score"] = None

    total_rows = len(df)
    with tqdm(total=total_rows, desc="Processing Rows") as pbar:
        for index, row in df.iterrows():
            row = process_row(row, sentiment_models)
            df.loc[index] = row
            pbar.update(1)

            # Update progress bar description
            pbar.set_postfix({"Completed": index+1})

    return df


In [4]:
df19 = pd.read_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2019_seperate_assessed_3.csv')



In [5]:
df21= pd.read_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_seperate_assessed_3.csv')


In [6]:
df_1 = assess_sentiment(df21[:100])
df_1.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_1_FIRST_seperate_assessed_5.csv', index=False)

<ipython-input-3-7b3becf55e09>:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[sentiment_column + "_average_score"] = None
<ipython-input-3-7b3becf55e09>:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[sentiment_column + "_average_score"] = None
<ipython-input-3-7b3becf55e09>:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

Xformers is not installed correctly. If you want to use memorry_efficient_attention to accelerate training use the following command to install Xformers
pip install xformers.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a B

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifie

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifie

Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.weight', 'lm_loss.bias']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['logits_proj.weight', 'logits_proj.bias', 'sequence_summary.summary.weight', 'sequence_summary.summary.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions a

Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.weight', 'lm_loss.bias']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['logits_proj.weight', 'logits_proj.bias', 'sequence_summary.summary.weight', 'sequence_summary.summary.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions a

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.weight', 'vocab_projector.bias', 'vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_layer_norm.weight']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.weight', 'pre_clas

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'roberta.pooler.dense.bias']
- This IS expect

In [7]:
df_2 = assess_sentiment(df21[100:200])
df_2.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_2_FIRST_seperate_assessed_5.csv', index=False)


Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.weight', 'pre_classifier.bias', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.weight', 'vocab_projector.bias', 'vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_layer_norm.weight']
- This IS expected if you are initializing DistilBertForSeq

In [8]:
df_3 = assess_sentiment(df21[200:300])
df_3.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_3_FIRST_seperate_assessed_5.csv', index=False)

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.weight', 'pre_classifier.bias', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.weight', 'vocab_projector.bias', 'vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_layer_norm.weight']
- This IS expected if you are initializing DistilBertForSeq

In [9]:
df_4 = assess_sentiment(df21[300:400])
df_4.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_4_FIRST_seperate_assessed_5.csv', index=False)

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.weight', 'pre_classifier.bias', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.weight', 'vocab_projector.bias', 'vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_layer_norm.weight']
- This IS expected if you are initializing DistilBertForSeq

In [10]:
df_5 = assess_sentiment(df21[400:500])
df_5.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_5_FIRST_seperate_assessed_5.csv', index=False)

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['logits_proj.weight', 'logits_proj.bias', 'sequence_summary.summary.weight', 'sequence_summary.summary.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.weight', 'lm_loss.bias']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertF

In [1]:
df_500 = pd.concat([df_1, df_2, df_3, df_4, df_5])
df_500
df_500.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_FIRST_seperate_assessed_5.csv', index=False)

NameError: ignored

In [ ]:
df_500.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_FIRST_seperate_assessed_5.csv', index=False)

In [11]:
import torch

In [12]:
import requests
from bs4 import BeautifulSoup
from transformers import pipeline
import pandas as pd
from tqdm import tqdm

def get_bbc_content(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content, "html.parser") 
    content = soup.find("div", attrs={"class": "gel-layout__item gel-2/3@l"})
    
    if content is None:
        content = soup.find("td", attrs={"class": "storybody"})
        if content is None:
            return None

    main_body = content.find_all('p')
    text = ""
    for i in main_body:
        text += i.text
    clean_text = text.replace('\n', ' ').replace('\xa0', '')
    return clean_text

def assess_bert_relevance(df):
    relevance_column = 'bert_relevance'
    model_name = 'bert-base-uncased'
    
    nlp = pipeline('text-classification', model=model_name)
    
    df[relevance_column] = None
    
    total_rows = len(df)
    
    with tqdm(total=total_rows, desc="Processing Rows") as pbar:
        for index, row in df.iterrows():
            content = get_bbc_content(row['url'])
            player_name = row['player']
            
            statement = f"{player_name} will be the MVP"
            
            relevance_score = nlp(statement, content)[0]['score']
            
            df.at[index, relevance_column] = relevance_score
            
            pbar.update(1)
            pbar.set_postfix({"Completed": index+1})
    
    return df


In [13]:
df_1 = assess_bert_relevance(df_1)
df_1.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_1_FIRST_seperate_assessed_6.csv', index=False)


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [14]:
df_2 = assess_bert_relevance(df_2)
df_2.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_2_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [16]:
df_3 = assess_bert_relevance(df_3)
df_3.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_3_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [17]:
df_4 = assess_bert_relevance(df_4)
df_4.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_4_FIRST_seperate_assessed_6.csv', index=False)


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [18]:
df_5 = assess_bert_relevance(df_5)
df_5.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_5_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [22]:
df_500_f = pd.concat([df_1, df_2, df_3, df_4, df_5])
df_500_f
df_500_f.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_FIRST_seperate_assessed_6.csv', index=False)


In [29]:
df_500_f

Unnamed: 0                                              title     date  \
0            19  NBA All-Star Game: Stephen Curry sets record a...  2021-22   
1            20  NBA: Marcus Smart on Stephen Curry injury - 'I...  2021-22   
2            24  NBA: Stephen Curry scores 40 points as Golden ...  2021-22   
3            25  Stephen Curry: Golden State Warriors star make...  2021-22   
4            26  NBA: Stephen Curry returns in Golden State War...  2021-22   
..          ...                                                ...      ...   
495        4136  NBA: LeBron James' comeback spoiled as Boston ...  2021-22   
496        4137  LeBron James scores 100th triple-double but LA...  2021-22   
497        4138  NBA: LeBron James scores 30-point triple-doubl...  2021-22   
498        4139  NBA: Giannis Antetokounmpo and LeBron James sh...  2021-22   
499        4140  NBA: Lebron James inspires LA Lakers to overti...  2021-22   

                                                 url         player  \
0    https://www.bbc.co.uk/sport/basketball/60459972  Stephen Curry   
1    https://www.bbc.co.uk/sport/basketball/60776514  Stephen Curry   
2    https://www.bbc.co.uk/sport/basketball/60200633  Stephen Curry   
3    https://www.bbc.co.uk/sport/basketball/60094949  Stephen Curry   
4    https://www.bbc.co.uk/sport/basketball/59738962  Stephen Curry   
..                                               ...            ...   
495  https://www.bbc.co.uk/sport/basketball/59358572   LeBron James   
496  https://www.bbc.co.uk/sport/basketball/59605658   LeBron James   
497  https://www.bbc.co.uk/sport/basketball/59588856   LeBron James   
498  https://www.bbc.co.uk/sport/basketball/59619765   LeBron James   
499  https://www.bbc.co.uk/sport/basketball/59413703   LeBron James   

     textblob_Sentiment  key_words_score sentiment_bert_average_score  \
0              0.014035              1.2                     0.639877   
1              0.050696              1.0                     0.607332   
2              0.223064              1.0                     0.592383   
3              0.082361              1.0                     0.602251   
4              0.092593              1.0                     0.559633   
..                  ...              ...                          ...   
495            0.250469              1.0                     0.693951   
496            0.004167              1.0                     0.531009   
497            0.222727              1.2                     0.606196   
498            0.253314              1.0                     0.631511   
499           -0.009259              1.0                      0.58951   

    sentiment_roberta_average_score sentiment_xlnet_average_score  \
0                          0.555403                      0.594191   
1                          0.533611                      0.565681   
2                          0.516726                      0.606547   
3                          0.550577                      0.573283   
4                          0.540382                      0.591025   
..                              ...                           ...   
495                        0.528271                      0.561165   
496                         0.54227                      0.610015   
497                        0.527521                      0.579298   
498                        0.513979                      0.591639   
499                         0.51745                      0.579309   

    sentiment_distilbert_average_score bert_relevance  
0                             0.539487       0.521457  
1                             0.523575       0.521457  
2                              0.52443       0.521457  
3                             0.529416       0.521457  
4                             0.528231       0.521457  
..                                 ...            ...  
495                           0.523535       0.648014  
496                           0.515323       0.64

In [23]:
df_500_f.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_FIRST_seperate_assessed_6.csv', index=False)

In [24]:
df20 = pd.read_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2020_seperate_assessed_4.csv')


In [25]:
df20

Unnamed: 0                                              title     date  \
0        300.0  NBA: LA Lakers lose to Portland as Atlanta Haw...  2020-21   
1        933.0  NBA: Joel Embiid returns from injury in Philad...  2020-21   
2        951.0  NBA: LeBron James stars against Oklahoma City ...  2020-21   
3       1250.0  LeBron James: NBA star's voting rights group s...  2020-21   
4       1428.0  NBA: Joel Embiid stars as Philadelphia 76ers b...  2020-21   
5       1786.0  Houston Rockets suffer overtime loss to Portla...  2020-21   
6       2093.0  NBA: LA Lakers and LA Clippers win, Boston Cel...  2020-21   
7       2124.0  NBA: Minnesota Timberwolves' Karl-Anthony Town...  2020-21   
8       2348.0  LaMelo Ball: Charlotte Hornets rookie becomes ...  2020-21   
9       2364.0        NBA: Houston Rockets beat San Antonio Spurs  2020-21   
10      2365.0  NBA: LeBron James and Anthony Davis shine as L...  2020-21   
11      2674.0  NBA: Kevin Durant leads Brooklyn Nets to victo...  2020-21   
12      2716.0  NBA round-up: Luka Doncic stars but Dallas Mav...  2020-21   
13      2717.0  NBA: Giannis Antetokounmpo shines as Milwaukee...  2020-21   
14      3239.0  NBA: Fans ejected after argument with LeBron J...  2020-21   
15      3414.0  NBA: Jimmy Butler stars as Miami Heat beat Uta...  2020-21   
16      4127.0  Leeds United 1-0 Burnley: Patrick Bamford hits...  2020-21   
17      4407.0                                          Episode 2  2020-21   
18      5207.0  NBA: Utah Jazz beat Philadelphia 76ers to enha...  2020-21   
19      5212.0  NBA All-Star Game: Giannis Antetokounmpo MVP a...  2020-21   
20      5484.0  NBA: Minnesota Timberwolves' Karl-Anthony Town...  2020-21   
21      7234.0  Premiership: Harlequins 24-12 Sale Sharks - Jo...  2020-21   
22      9028.0  Brooklyn Nets beat Orlando Magic for eighth st...  2020-21   

                                                  url              player  \
0     https://www.bbc.co.uk/sport/basketball/55473013      Damian Lillard   
1     https://www.bbc.co.uk/sport/basketball/56630066         Luka Dončić   
2     https://www.bbc.co.uk/sport/basketball/56022204         Luka Dončić   
3   https://www.bbc.co.uk/news/world-us-canada-563...        LeBron James   
4     https://www.bbc.co.uk/sport/basketball/55643741    Donovan Mitchell   
5     https://www.bbc.co.uk/sport/basketball/55458404         CJ McCollum   
6     https://www.bbc.co.uk/sport/basketball/55615129       Kawhi Leonard   
7     https://www.bbc.co.uk/sport/basketball/55687220       Kawhi Leonard   
8     https://www.bbc.co.uk/sport/basketball/55608161        Nikola Jokić   
9     https://www.bbc.co.uk/sport/basketball/55673146        Nikola Jokić   
10    https://www.bbc.co.uk/sport/basketball/55556627        Nikola Jokić   
11    https://www.bbc.co.uk/sport/basketball/56060272    Bojan Bogdanović   
12    https://www.bbc.co.uk/sport/basketball/55701549       Julius Randle   
13    https://www.bbc.co.uk/sport/basketball/55542453       Julius Randle   
14    https://www.bbc.co.uk/sport/basketball/55899796        Jrue Holiday   
15    https://www.bbc.co.uk/sport/basketball/56221356        Jimmy Butler   
16      https://www.bbc.co.uk/sport/football/55382725     Harrison Barnes   
17          https://www.bbc.co.uk/programmes/p098hdcr          Joe Harris   
18    https://www.bbc.co.uk/sport/basketball/56061283         Ben Simmons   
19    https://www.bbc.co.uk/sport/basketball/56318297         Ben Simmons   
20    https://www.bbc.co.uk/sport/basketball/55687220  Karl-Anthony Towns   
21   https://www.bbc.co.uk/sport/rugby-union/56111636       Marcus Morris   
22    https://www.bbc.co.uk/sport/basketball/56207442        Kyrie Irving   

    textblob_Sentiment  key_words_score  nltk_Sentiment  
0             0.056967              1.0          0.9913  
1             0.155437              0.6          0.9702  
2             0.039713              0.6          0.9910  
3            -0.013361              0.0           

In [26]:
df_20 = assess_sentiment(df20)

Processing Rows:   0%|          | 0/23 [00:00<?, ?it/s]Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassific

In [27]:
df_20_1 = assess_bert_relevance(df_20)
df_20_1.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2020_seperate_assessed_6.csv', index=False)
df_20_1

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

Unnamed: 0                                              title     date  \
0        300.0  NBA: LA Lakers lose to Portland as Atlanta Haw...  2020-21   
1        933.0  NBA: Joel Embiid returns from injury in Philad...  2020-21   
2        951.0  NBA: LeBron James stars against Oklahoma City ...  2020-21   
3       1250.0  LeBron James: NBA star's voting rights group s...  2020-21   
4       1428.0  NBA: Joel Embiid stars as Philadelphia 76ers b...  2020-21   
5       1786.0  Houston Rockets suffer overtime loss to Portla...  2020-21   
6       2093.0  NBA: LA Lakers and LA Clippers win, Boston Cel...  2020-21   
7       2124.0  NBA: Minnesota Timberwolves' Karl-Anthony Town...  2020-21   
8       2348.0  LaMelo Ball: Charlotte Hornets rookie becomes ...  2020-21   
9       2364.0        NBA: Houston Rockets beat San Antonio Spurs  2020-21   
10      2365.0  NBA: LeBron James and Anthony Davis shine as L...  2020-21   
11      2674.0  NBA: Kevin Durant leads Brooklyn Nets to victo...  2020-21   
12      2716.0  NBA round-up: Luka Doncic stars but Dallas Mav...  2020-21   
13      2717.0  NBA: Giannis Antetokounmpo shines as Milwaukee...  2020-21   
14      3239.0  NBA: Fans ejected after argument with LeBron J...  2020-21   
15      3414.0  NBA: Jimmy Butler stars as Miami Heat beat Uta...  2020-21   
16      4127.0  Leeds United 1-0 Burnley: Patrick Bamford hits...  2020-21   
17      4407.0                                          Episode 2  2020-21   
18      5207.0  NBA: Utah Jazz beat Philadelphia 76ers to enha...  2020-21   
19      5212.0  NBA All-Star Game: Giannis Antetokounmpo MVP a...  2020-21   
20      5484.0  NBA: Minnesota Timberwolves' Karl-Anthony Town...  2020-21   
21      7234.0  Premiership: Harlequins 24-12 Sale Sharks - Jo...  2020-21   
22      9028.0  Brooklyn Nets beat Orlando Magic for eighth st...  2020-21   

                                                  url              player  \
0     https://www.bbc.co.uk/sport/basketball/55473013      Damian Lillard   
1     https://www.bbc.co.uk/sport/basketball/56630066         Luka Dončić   
2     https://www.bbc.co.uk/sport/basketball/56022204         Luka Dončić   
3   https://www.bbc.co.uk/news/world-us-canada-563...        LeBron James   
4     https://www.bbc.co.uk/sport/basketball/55643741    Donovan Mitchell   
5     https://www.bbc.co.uk/sport/basketball/55458404         CJ McCollum   
6     https://www.bbc.co.uk/sport/basketball/55615129       Kawhi Leonard   
7     https://www.bbc.co.uk/sport/basketball/55687220       Kawhi Leonard   
8     https://www.bbc.co.uk/sport/basketball/55608161        Nikola Jokić   
9     https://www.bbc.co.uk/sport/basketball/55673146        Nikola Jokić   
10    https://www.bbc.co.uk/sport/basketball/55556627        Nikola Jokić   
11    https://www.bbc.co.uk/sport/basketball/56060272    Bojan Bogdanović   
12    https://www.bbc.co.uk/sport/basketball/55701549       Julius Randle   
13    https://www.bbc.co.uk/sport/basketball/55542453       Julius Randle   
14    https://www.bbc.co.uk/sport/basketball/55899796        Jrue Holiday   
15    https://www.bbc.co.uk/sport/basketball/56221356        Jimmy Butler   
16      https://www.bbc.co.uk/sport/football/55382725     Harrison Barnes   
17          https://www.bbc.co.uk/programmes/p098hdcr          Joe Harris   
18    https://www.bbc.co.uk/sport/basketball/56061283         Ben Simmons   
19    https://www.bbc.co.uk/sport/basketball/56318297         Ben Simmons   
20    https://www.bbc.co.uk/sport/basketball/55687220  Karl-Anthony Towns   
21   https://www.bbc.co.uk/sport/rugby-union/56111636       Marcus Morris   
22    https://www.bbc.co.uk/sport/basketball/56207442        Kyrie Irving   

    textblob_Sentiment  key_words_score  nltk_Sentiment  \
0             0.056967              1.0          0.9913   
1             0.155437              0.6          0.9702   
2             0.039713              0.6          0.9910   
3            -0.013361              0.0       